In [1]:
# Check Environment

import sys
print(sys.version)
print(sys.executable)

3.7.5 (default, Oct 31 2019, 15:18:51) [MSC v.1916 64 bit (AMD64)]
C:\Users\Dennis\anaconda3\envs\rc_env_np16p6\python.exe


In [2]:
# IMPORTS

import rescomp
import numpy as np

import pandas as pd

import plotly.express as px

import matplotlib.pyplot as plt
# from mpl_toolkits import mplot3d

import scipy

### Create Lorenz Dataset:

In [3]:
simulation_time_steps = 8000
dt = 2e-2

starting_point = np.array([-14.03020521, -20.88693127, 25.53545])
sim_data = rescomp.simulate_trajectory(
    sys_flag='lorenz', dt=dt, time_steps=simulation_time_steps,
    starting_point=starting_point)

### Create artificially "wrong" model and plot real and "fake" Lorenz Attractor:

In [4]:
#Create artificially "wrong" model by changing the system parameters:
eps1 = 0.0
eps2 = 0.0
eps3 = 0.0
model = lambda x: rescomp.simulations._normal_lorenz(x, sigma=10*(1+eps1), rho=28*(1+eps2), beta=8/3*(1+eps3))
# model = lambda x: -x

# model_pred = lambda x: x + model(x)*dt
model_pred = lambda x: rescomp.simulations._runge_kutta(model, dt, x)

# test it:
x = np.zeros((simulation_time_steps, 3))

x[0] = starting_point
for i in range(1, simulation_time_steps):
    x_i = x[i-1]
    x[i] = model_pred(x_i)


# Plotly
sim_data_df = pd.DataFrame(data=sim_data, columns = ["x", "y", "z"])
sim_data_df["name"] = "true"
wrong_model_data_df = pd.DataFrame(data=x, columns = ["x", "y", "z"])
wrong_model_data_df["name"] = "wrong"
df = pd.concat([sim_data_df, wrong_model_data_df])
fig = px.line_3d(df, x = "x", y ="y", z="z", color = "name")
fig.show()


# Matplotlib: 
# fig = plt.figure(figsize=(6, 3), dpi=300)
# ax = fig.add_subplot(111, projection='3d')
# ax.plot(x[:, 0], x[:, 1], x[:, 2],
#         alpha=0.8, color='blue', linewidth = 0.1)
# ax.plot(sim_data[:, 0], sim_data[:, 1], sim_data[:, 2],
#         alpha=0.8, color='red', linewidth = 0.1)
# ax.set_title("Normal Lorenz63 System Simulated")
# ax.set_xlabel('x')
# ax.set_ylabel('y')
# ax.set_zlabel('z')
# plt.show()

### Create "normal" and different Hybrid Models:

In [16]:
n_dim = 1000

ESNs = {}
settings_dict = {}

# The Baseline
np.random.seed(1)
name = "normal"
esn_normal = rescomp.esn.ESNWrapper()
esn_normal.create_network(n_dim = n_dim)
ESNs[name] = esn_normal

# Hybrid only at output: 
np.random.seed(1)
name = "hybrid out"
esn_hybrid_out = rescomp.esn.ESNHybrid()
esn_hybrid_out.create_network(n_dim = n_dim)
add_model_to_output = True
add_model_to_input = False
esn_hybrid_out.set_model(model_pred, add_model_to_input = add_model_to_input, add_model_to_output = add_model_to_output)
ESNs[name] = esn_hybrid_out

# Hybrid only at input:
np.random.seed(1)
name = "hybrid in"
esn_hybrid_in = rescomp.esn.ESNHybrid()
esn_hybrid_in.create_network(n_dim = n_dim)
add_model_to_output = False
add_model_to_input = True
gamma = 0.5
esn_hybrid_in.set_model(model_pred, add_model_to_input = add_model_to_input,
                        add_model_to_output = add_model_to_output,
                       gamma = gamma)
ESNs[name] = esn_hybrid_in

# Hybrid at in- and output: 
np.random.seed(1)
name = "hybrid both"
esn_hybrid_both = rescomp.esn.ESNHybrid()
esn_hybrid_both.create_network(n_dim = n_dim)
add_model_to_output = True
add_model_to_input = True
gamma = 0.5
esn_hybrid_both.set_model(model_pred, add_model_to_input = add_model_to_input,
                        add_model_to_output = add_model_to_output,
                       gamma = gamma)
ESNs[name] = esn_hybrid_both

# The Test
np.random.seed(1)
name = "HybridDoan1"
esn_normal = rescomp.esn.ESNWrapper()
esn_normal.create_network(n_dim = n_dim, )
ESNs[name] = esn_normal
train_fractions = (1,1,1)
train_fractions = np.array(train_fractions)/np.array(train_fractions).sum()
print(train_fractions)

# The Test
np.random.seed(1)
name = "HybridDoan2"
esn_normal = rescomp.esn.ESNWrapper()
esn_normal.create_network(n_dim = n_dim, )
ESNs[name] = esn_normal
# train_fractions = (1,2,1)
# train_fractions = np.array(train_fractions)/np.array(train_fractions).sum()
# print(train_fractions)

[0.33333333 0.33333333 0.33333333]


### Train and predict:

In [17]:
def split_train_steps(train_fractions, train_steps):
    x_train_steps_1 = int(train_fractions[0]*train_steps)
    x_train_steps_2 = train_steps - x_train_steps_1
    x_train_steps_21 = int((train_fractions[1]/(train_fractions[1:].sum()))*x_train_steps_2)
    x_train_steps_22 = x_train_steps_2 - x_train_steps_21
    print(x_train_steps_1, x_train_steps_21,x_train_steps_22)
    return x_train_steps_1, x_train_steps_21, x_train_steps_22
split_train_steps(train_fractions, train_steps)

1666 1667 1667


(1666, 1667, 1667)

In [20]:
# DOAN Hybrid:


def physical_error_doan(weights, esn, model, x_train_doan_data_post, x_train_steps21, x_train_steps22, w_shape, dt):
    # DOI: 10.1098/rspa.2021.0135
    # first predict
    esn._w_out = weights.reshape(w_shape)
    y_pred, y_test = esn.predict(x_train_doan_data_post)
    # print(x_train_doan_data_post.shape, x_train_steps21, x_train_steps22)
    y_pred_1, y_test_1 = y_pred[:x_train_steps21], y_test[:x_train_steps21]
    
    y_pred_2, y_test_2 = y_pred[x_train_steps21:], y_test[x_train_steps21:]
    
    
    error_1 = np.mean(np.linalg.norm(y_pred_1 - y_test_1, axis = 1))
    
    gradient_pred = (y_pred_2[1:] - y_pred_2[:-1])/dt
    gradient_pred_model = model(y_pred_2[:-1])
    F = gradient_pred - gradient_pred_model
    
    error_2 = np.mean(np.linalg.norm(F , axis = 1))
    print(error_1, error_2)
    return error_1 + error_2

def physical_error_doan_fast(weights, R, model, x_train_doan_data_post, x_train_steps21, x_train_steps22, w_shape, dt):
    # DOI: 10.1098/rspa.2021.0135
    # first predict
    
    w = weights.reshape(w_shape)
#     print(w.shape)
#     print(r.shape)
    y_pred = (w @ R.T).T
    y_test = x_train_doan_data_post[1:]
#     print(y_pred.shape)
#     print(y_test.shape)
    # print(x_train_doan_data_post.shape, x_train_steps21, x_train_steps22)
    y_pred_1, y_test_1 = y_pred[:x_train_steps21], y_test[:x_train_steps21]
    
    y_pred_2, y_test_2 = y_pred[x_train_steps21:], y_test[x_train_steps21:]
    
    
    error_1 = np.mean(np.linalg.norm(y_pred_1 - y_test_1, axis = 1))
    print(error_1)
    return error_1
    gradient_pred = (y_pred_2[1:] - y_pred_2[:-1])/dt
    gradient_pred_model = model(y_pred_2[:-1])
#     print(gradient_pred.shape)
#     print(gradient_pred_model.shape)

    F = gradient_pred - gradient_pred_model
    
    error_2 = np.mean(np.linalg.norm(F , axis = 1))
    print(error_1, error_2, error_1 + error_2)
    
    return error_1 + error_2

def model_array(x):
#     print("X.shape, ", x.shape)
    sigma=10*(1+eps1)
    rho=28*(1+eps2)
    beta=8/3*(1+eps3)
    return np.array([sigma * (x[:, 1] - x[:, 0]),
                 x[:, 0] * (rho - x[:, 2]) - x[:, 1],
                 x[:, 0] * x[:, 1] - beta * x[:, 2]]).T


In [21]:
# second try Faster
train_sync_steps = 500
train_steps = 5000
pred_steps = 1500 

# For testing different W_in settings
w_in_sparse=True #True
w_in_ordered=True #False
w_in_no_update=False #False
act_fct_flag='tanh_simple' #'tanh_simple'
w_out_fit_flag="simple" #"simple"
reg_param = 1e-6

ESNs_results = {}

for name, ESN in ESNs.items():
    print("---- Training and predicting " + name + " ----")
    
    if name.startswith("HybridDoan"):
        x_train_steps_1, x_train_steps_21, x_train_steps_22 = split_train_steps(train_fractions, train_steps)
        x_train_doan_data_pre = sim_data[:train_sync_steps + x_train_steps_1]
        x_train_doan_data_post = sim_data[train_sync_steps + x_train_steps_1 - 1: train_sync_steps + x_train_steps_1 + 
                                         x_train_steps_21 + x_train_steps_22]
        ESN.train(x_train=x_train_doan_data_pre, sync_steps=train_sync_steps, reg_param=reg_param, 
             w_in_sparse=w_in_sparse, 
             w_in_ordered=w_in_ordered, w_in_no_update=w_in_no_update, act_fct_flag=act_fct_flag, 
             w_out_fit_flag=w_out_fit_flag)
        r = ESN.synchronize(x_train_doan_data_post[:-1], save_r=True)
        print("r.shape: ", r.shape)
        if name == "HybridDoan1":

            initial_w = ESN.get_w_out().flatten()
            w_shape = ESN.get_w_out().shape

            args = (r, model_array, x_train_doan_data_post, x_train_steps_21, x_train_steps_22, w_shape, dt)
            opt_results = scipy.optimize.minimize(fun = physical_error_doan_fast, x0 = initial_w, method = "L-BFGS-B", 
                                                  args = args) #, options = {"maxiter": 50}
            optimized_w = opt_results["x"]
            # ESN._w_out = optimized_w.reshape(w_shape)
        
    else:
       # continue
        ESN.train(x_train=sim_data[:train_sync_steps + train_steps], sync_steps=train_sync_steps, reg_param=reg_param, 
             w_in_sparse=w_in_sparse, 
             w_in_ordered=w_in_ordered, w_in_no_update=w_in_no_update, act_fct_flag=act_fct_flag, 
             w_out_fit_flag=w_out_fit_flag)
    
    out = ESN.predict(sim_data[train_sync_steps + train_steps-1:])
    ESNs_results[name] = out


---- Training and predicting normal ----
---- Training and predicting hybrid out ----
---- Training and predicting hybrid in ----
---- Training and predicting hybrid both ----
---- Training and predicting HybridDoan1 ----
1666 1667 1667
r.shape:  (3334, 1000)
0.003189966964770655
0.0031899670320776514
0.0031899668954770873
0.0031899668986142046
0.0031899669119469726
0.003189966950018328
0.0031899668972146106
0.0031899670257446774
0.0031899670316295255
0.003189966900018854
0.003189966943366916
0.0031899668975570537
0.003189966898655213
0.003189967031080307
0.0031899668978058555
0.003189967032206163
0.003189966914931131
0.0031899668985005156
0.003189967032539261
0.003189966977885521
0.0031899670282505197
0.0031899668979858153
0.003189967031543421
0.0031899670160240386
0.0031899670157428217
0.0031899668988244344
0.003189966901389283
0.003189966940816569
0.0031899669020726052
0.0031899670266380205
0.0031899669080055404
0.003189967031421388
0.003189967032073902
0.003189967015764571
0.003189

0.003189966918799365
0.003189966916936172
0.0031899669430682197
0.003189967010954911
0.0031899670084601273
0.0031899670104526025
0.0031899670145599337
0.0031899669195415595
0.0031899670065300856
0.0031899670122198616
0.00318996691783858
0.003189967000051767
0.00318996691858175
0.0031899669204130086
0.003189967006584458
0.003189966918791554
0.0031899669320974333
0.003189966919889148
0.0031899669180077248
0.0031899670114667066
0.0031899669184160457
0.0031899670119670555
0.0031899670117506327
0.0031899669170380586
0.0031899669194984013
0.003189966918285439
0.0031899670100642447
0.003189966918338696
0.003189967013401897
0.0031899669178254036
0.0031899670103105134
0.003189967009420136
0.0031899670107670263
0.003189966917364656
0.0031899669200566904
0.003189967010132952
0.0031899670122439707
0.003189966955794206
0.0031899670131453135
0.0031899670110720345
0.003189967010773866
0.0031899669122297564
0.003189966918959547
0.003189966916866857
0.0031899670113237953
0.00318996691815987
0.003189966

0.0031899668747835774
0.0031899670578822187
0.003189966871793363
0.00318996687172782
0.0031899670578821944
0.003189966871726047
0.003189966871723931
0.00318996687172742
0.0031899668718377234
0.003189966871832065
0.003189966871723971
0.003189966871734294
0.0031899670578774586
0.0031899670578822022
0.003189966871723944
0.003189967057882203
0.003189966871723942
0.0031899668731667536
0.003189967057715493
0.003189966872220908
0.0031899670574728083
0.0031899670578807372
0.003189967055148278
0.0031899668953086257
0.003189966871814304
0.0031899670578277727
0.003189967057882131
0.0031899669800931714
0.0031899668717240205
0.0031899670578784418
0.0031899669319690105
0.003189966871723941
0.003189967057772123
0.003189966871726065
0.0031899670578653507
0.0031899668717242703
0.0031899670578816723
0.0031899668723875045
0.003189967057881964
0.0031899670578798677
0.003189966871754234
0.0031899668717239303
0.0031899670470455035
0.0031899670578822083
0.0031899669726438225
0.0031899670558279162
0.003189966

0.003189966304496904
0.0031899663005203207
0.0031899664129239665
0.003189967630946094
0.0031899674675000397
0.003189966299398991
0.0031899676257846833
0.003189967581826696
0.003189967495332964
0.0031899676286023543
0.0031899662987059443
0.0031899663253930764
0.0031899663032673178
0.003189966297209675
0.003189966304409146
0.003189966311300487
0.003189967509630115
0.0031899676184003797
0.0031899663105626076
0.0031899662970344875
0.0031899673272021167
0.0031899674504848215
0.003189966369834138
0.003189966324548936
0.0031899665260063967
0.0031899663093395373
0.0031899675836802813
0.0031899663238974547
0.00318996636573465
0.003189966372691075
0.0031899665646797997
0.0031899663849512616
0.0031899675705609077
0.0031899664558229035
0.003189966450609829
0.003189967625890568
0.0031899674367640665
0.003189967626841111
0.0031899676294526876
0.0031899676272433924
0.0031899670814713216
0.003189967523629735
0.0031899662980884743
0.0031899676078807177
0.0031899666235825483
0.003189967619566665
0.00318

0.0031899662739922527
0.003189967067023866
0.003189966269741142
0.0031899676522347113
0.0031899666480491506
0.0031899675363959525
0.00318996765630439
0.0031899676603514815
0.003189966275461448
0.003189967644152932
0.0031899662755193853
0.0031899662768137722
0.0031899662657406177
0.003189966309543403
0.003189967642606425
0.0031899662762120647
0.0031899676526814316
0.0031899676594652616
0.0031899662713974195
0.003189966276958295
0.0031899664682451395
0.0031899662761874824
0.0031899663078998734
0.0031899662773961592
0.003189966266816669
0.0031899662749582994
0.0031899664622521196
0.0031899676584727183
0.0031899676548231915
0.003189966300983848
0.003189966268303787
0.003189966276212617
0.0031899663965679332
0.003189967620522802
0.0031899676520350017
0.0031899664256640923
0.003189966275124037
0.0031899662787070746
0.003189967652480177
0.0031899662744853375
0.0031899673169016574
0.0031899676138794557
0.0031899673746987787
0.0031899676396092524
0.003189966268130045
0.003189966279070167
0.0031

...

0.0031793753863915176
0.003179375352516339
0.003179376370420767
0.0031793753847122346
0.0031793763709288833
0.003179375947918787
0.0031793753873147978
0.003179376389056597
0.0031793763861183238
0.0031793756998290223
0.0031793753910288043
0.00317937609237664
0.0031793756543012927
0.003179375671238397
0.0031793753806979327
0.003179376250907023
0.003179375374857286
0.0031793763975996848
0.0031793763243704127
0.0031793757907601127
0.003179376034357117
0.003179375402058806
0.003179376241585432
0.0031793759259088677
0.00317937617467836
0.0031793755703450424
0.0031793760761055292
0.00317937594130283
0.0031793762176804486
0.00317937625493101
0.003179376247185158
0.00317937550350207
0.0031793755211520654
0.0031793758956459085
0.003179375495026539
0.0031793755993531217
0.0031793757015551472
0.003179375608305857
0.0031793762484643344
0.003179375494106187
0.003179376265747419
0.0031793762667230107
0.003179376025683991
0.003179376205992118
0.0031793755514747534
0.0031793759941384256
0.0031793755310

0.003179375717232426
0.003179375717328767
0.00317937604485773
0.00317937571723618
0.0031793757172320944
0.0031793760448526696
0.0031793760448575134
0.003179376044849817
0.0031793760468355058
0.003179375717231192
0.003179376044857766
0.0031793760447698994
0.0031793757172372743
0.0031793757157405175
0.0031793760448449544
0.0031793757172384105
0.0031793757160438157
0.0031793759006920443
0.0031793757172316832
0.003179375717264756
0.003179376044736136
0.0031793760447205444
0.003179375717498046
0.0031793760448572943
0.00317937604477967
0.003179376044847546
0.0031793760448403713
0.0031793757172313615
0.0031793757172310384
0.0031793760448509583
0.003179376044809226
0.003179375717231007
0.0031793757166306493
0.003179376044857612
0.003179375717233953
0.003179375717174809
0.0031793760449079812
0.003179375717249356
0.003179376046110154
0.0031793760448074176
0.0031793757173426375
0.003179375717245025
0.0031793760448575775
0.0031793757172313476
0.0031793760446783515
0.0031793757169320353
0.003179375

0.0031793758128295605
0.00317937594949556
0.0031793759118745077
0.00317937598104678
0.0031793758151664278
0.003179375806286891
0.0031793759443117142
0.003179375812151283
0.003179375952546495
0.0031793759501275664
0.003179375949448727
0.003179375948108586
0.0031793758858637325
0.003179375947868555
0.003179375813955223
0.0031793759472288864
0.0031793759499120174
0.0031793759483558
0.0031793759521234364
0.0031793759743569063
0.0031793759557659294
0.003179375948982239
0.003179375812002361
0.0031793759586707633
0.0031793758133644634
0.00317937596951829
0.003179375947701493
0.003179375947972804
0.0031793759737781596
0.0031793757996532277
0.0031793758079382258
0.003179375972956519
0.003179375948278023
0.003179375949641113
0.00317937595084466
0.0031793759458304885
0.0031793757969332307
0.0031793759478807577
0.003179375814578858
0.0031793759486774473
0.0031793758909285383
0.0031793758108989273
0.003179375810530148
0.003179375789989176
0.003179375810275522
0.003179375815995504
0.0031793758134665

0.00317937600915026
0.0031793759233705024
0.0031793758655880057
0.003179375994706508
0.0031793759012574726
0.003179375941723846
0.0031793759526432294
0.003179375993315012
0.0031793758608291652
0.003179375763125351
0.0031793757626164443
0.003179375766376017
0.003179375748969012
0.0031793757541306376
0.0031793757915257654
0.003179376000534077
0.003179375889996265
0.0031793757707809724
0.003179375759581496
0.0031793759709127603
0.0031793759129476913
0.0031793758084167653
0.003179376001503912
0.0031793760009582893
0.003179375804475086
0.0031793759712392938
0.0031793757524391977
0.0031793760071098572
0.003179375894389629
0.003179375975609874
0.00317937582533555
0.003179375825137291
0.0031793760117419085
0.0031793757948895573
0.0031793759793527655
0.003179375759225477
0.003179375792099376
0.003179375990264706
0.003179375983935008
0.0031793759183554086
0.003179375851534927
0.003179375888699239
0.0031793758986908794
0.0031793758356907544
0.0031793757939407668
0.003179375822960809
0.00317937575

0.0031793758533668654
0.003179375853511274
0.0031793758531378424
0.003179375852016253
0.0031793758535117564
0.0031793759116357516
0.0031793758535116788
0.0031793758535117417
0.003179375852328547
0.0031793759085921645
0.0031793759085732066
0.0031793758535063207
0.003179375853511706
0.0031793758781159726
0.003179375849417319
0.003179375853511736
0.003179375908572625
0.003179375908584172
0.0031793758493806378
0.0031793758529942693
0.003179375853511635
0.00317937585351006
0.003179375908572622
0.003179375909039177
0.0031793758535088846
0.0031793759087101006
0.0031793759085728796
0.0031793758975374427
0.0031793759085727955
0.003179375908575072
0.0031793758535092853
0.0031793759091048703
0.003179375914071501
0.003179375853504522
0.0031793758714577067
0.003179375853511637
0.0031793758534314474
0.0031793759104157262
0.0031793759104208727
0.003179375853245602
0.003179375908572693
0.0031793758525279652
0.0031793759098497887
0.0031793758535114676
0.003179375853493863
0.003179375852453638
0.0031793

In [ ]:
(initial_w.reshape(w_shape) - optimized_w.reshape(w_shape)).max()
opt_results

In [ ]:
# # first try (TOO SLOW)
# train_sync_steps = 500
# train_steps = 6000
# pred_steps = 1500 

# # For testing different W_in settings
# w_in_sparse=True #True
# w_in_ordered=True #False
# w_in_no_update=False #False
# act_fct_flag='tanh_simple' #'tanh_simple'
# w_out_fit_flag="simple" #"simple"
# reg_param = 1e-10

# ESNs_results = {}

# for name, ESN in ESNs.items():
#     print("---- Training and predicting " + name + " ----")
    
#     if name == "HybridDoan":
#         x_train_steps_1, x_train_steps_21, x_train_steps_22 = split_train_steps(train_fractions, train_steps)
#         x_train_doan_data_pre = sim_data[:train_sync_steps + x_train_steps_1]
#         x_train_doan_data_post = sim_data[train_sync_steps + x_train_steps_1 - 1: train_sync_steps + x_train_steps_1 + 
#                                          x_train_steps_21 + x_train_steps_22]
#         ESN.train(x_train=x_train_doan_data_pre, sync_steps=train_sync_steps, reg_param=reg_param, 
#              w_in_sparse=w_in_sparse, 
#              w_in_ordered=w_in_ordered, w_in_no_update=w_in_no_update, act_fct_flag=act_fct_flag, 
#              w_out_fit_flag=w_out_fit_flag)
#         initial_w = ESN.get_w_out().flatten()
#         w_shape = ESN.get_w_out().shape

#         args = (ESN, model_array, x_train_doan_data_post, x_train_steps_21, x_train_steps_22, w_shape, dt)
#         optimized_w = scipy.optimize.minimize(fun = physical_error_doan, x0 = initial_w, method = "L-BFGS-B", 
#                                               args = args, options = {"maxiter": 10})
#         ESN._w_out = w_shape.reshape(w_shape)
    
#     else:
#        # continue
#         ESN.train(x_train=sim_data[:train_sync_steps + train_steps], sync_steps=train_sync_steps, reg_param=reg_param, 
#              w_in_sparse=w_in_sparse, 
#              w_in_ordered=w_in_ordered, w_in_no_update=w_in_no_update, act_fct_flag=act_fct_flag, 
#              w_out_fit_flag=w_out_fit_flag)
    
#     out = ESN.predict(sim_data[train_sync_steps + train_steps-1:])
#     ESNs_results[name] = out


### Create Dataframe used for plotting (plotly):

In [22]:
frames = []

get_test = True
for name, result in ESNs_results.items():
    y_pred, y_test = result
    
    if get_test:
        df_test = pd.DataFrame(data=y_test, columns = ["x", "y", "z"])
        df_test["name"] = "test"
        frames.append(df_test)
        get_test = False
    df_pred = pd.DataFrame(data=y_pred, columns = ["x", "y", "z"])
    df_pred["name"] = name + " pred"
    frames.append(df_pred)
        
df = pd.concat(frames)
print(df)

             x          y          z              name
0     7.078758   9.436282  21.350475              test
1     7.577023  10.194632  21.643068              test
2     8.122111  10.944310  22.136152              test
3     8.700591  11.647650  22.839201              test
4     9.293697  12.257143  23.750784              test
...        ...        ...        ...               ...
2495 -0.857362  -3.224535  22.984680  HybridDoan2 pred
2496 -1.291085  -3.283875  21.860076  HybridDoan2 pred
2497 -1.663480  -3.417051  20.820688  HybridDoan2 pred
2498 -2.000378  -3.633849  19.863751  HybridDoan2 pred
2499 -2.323674  -3.936204  18.987944  HybridDoan2 pred

[17500 rows x 4 columns]


### Plot x coordinate of models: prediction vs test:

In [23]:
fig = px.line(df, y="x", color='name')
fig.show()

### Plot attractor: 

In [ ]:
fig = px.line_3d(df,x = "x", y ="y", z="z", color='name')
fig.show()

### Create Dataframe for RMSE:

In [ ]:
frames = []

for name, result in ESNs_results.items():
    y_pred, y_test = result
    rmse = rescomp.measures.rmse_over_time(y_pred, y_test)
    df_rmse = pd.DataFrame(data=rmse, columns = ["rmse"])
    df_rmse["name"] = "rmse " + name
    frames.append(df_rmse)
        
df_rmse = pd.concat(frames)
print(df_rmse)

### Plot RMSE:

In [ ]:
fig = px.line(df_rmse, y="rmse", color='name')
fig.show()

### Plot the average output weights (if model is added to output):

In [ ]:
def get_info_about_output_weights(esn):
    n_dim = esn._n_dim
    rc_weights = esn._w_out[:, : n_dim]
    model_weights = esn._w_out[:, n_dim:]
    

    
    avg_abs_rc_weight = np.average(np.abs(rc_weights))
    avg_abs_model_weight = np.average(np.abs(model_weights))
    return avg_abs_rc_weight, avg_abs_model_weight

for esn_name in ["hybrid out", "hybrid both"]:
    print("______________")
    print(f"{esn_name}: ")
    esn = ESNs[esn_name]
    avg_abs_rc_weight, avg_abs_model_weight = get_info_about_output_weights(esn)
    print(f"avg_abs_rc_weight: {avg_abs_rc_weight}")
    print(f"avg_abs_model_weight: {avg_abs_model_weight}")

# modify _w_out:
def get_modified_w_out(n_dim, state_dim):
    matrix = np.zeros((state_dim, n_dim))
    print(matrix)
    print(matrix[:, 0])
    for i in range(0,state_dim):
        to_add = np.zeros(state_dim)
        to_add[i] = 1
        matrix[:, n_dim - state_dim +i] = to_add
    return matrix

n_dim = 5
state_dim = 3
get_modified_w_out(n_dim, state_dim)

-----------------------------------
# OLD

In [ ]:
# print(esn_hybrid._w_out.shape)
# print(esn_normal._w_out.shape)

# print(np.average(esn_hybrid._w_out[:, -3:]))
# print(np.average(esn_hybrid._w_out[:, :-3]))

In [ ]:
# fig1 = plt.figure(figsize=(9, 6), dpi=300)
# ax1 = fig1.add_subplot(111, projection='3d')

# ax1.plot(y_test_normal[:, 0], y_test_normal[:, 1], y_test_normal[:, 2],
#         alpha=0.8, color='blue', label='simulation')
# ax1.plot(y_pred_normal[:, 0], y_pred_normal[:, 1], y_pred_normal[:, 2],
#         alpha=0.8, color='orange', label='pred normal')
# ax1.plot(y_pred_hybrid[:, 0], y_pred_hybrid[:, 1], y_pred_hybrid[:, 2],
#         alpha=0.8, color='red', label='pred hybrid')

# start = y_test_normal[0]
# ax1.plot([start[0]], [start[1]], [start[2]], 
#          color='black', linestyle='', marker='o', label='starting point')

# ax1.set_title("Simulation vs Prediction")
# ax1.set_xlabel('x')
# ax1.set_ylabel('y')
# ax1.set_zlabel('z')
# plt.legend()
# plt.show()

In [ ]:
# prediction_dict = {}

# y_test = None

# fig2 = plt.figure(figsize=(9, 6), dpi=300)
# ax2 = fig2.add_subplot(1, 1, 1)

# for name, prediction in prediction_dict.items():
#     rmse = rescomp.measures.rmse_over_time(time_series, y_test)
#     ax2.plot(rmse, linestyle='--', label=name)
#     print("AVG RMSE for " + name, np.average(rmse))

# ax2.set_title("RMSE")
# ax2.set_xlabel('time steps')
# ax2.set_ylabel('RMSE')
# plt.legend()
# plt.show()

In [ ]:
n_dim = 100
avg_deg = 3
p = 0.4 # largest eigenvalue (spectral radius)

esn1 = rescomp.esn.ESNWrapper()
esn1.create_network(n_dim = n_dim, n_rad=p, n_avg_deg=avg_deg, n_type_flag="erdos_renyi_directed")

esn2 = rescomp.esn.ESNWrapper()
esn2.create_network(n_dim = n_dim, n_rad=p, n_avg_deg=avg_deg, n_type_flag="erdos_renyi")


In [ ]:
print(np.argwhere(esn1._network).shape)
print("-----------------------------------------")
print(np.argwhere(esn2._network).shape)

In [ ]:
eps_list = np.linspace(0.004, 0.1, 25)
print(eps_list)

In [ ]:
r = np.ones((5, 5))*2
r = np.ones((5))*2

r_gen = np.copy(r)
r_gen.T[::2] = r.T[::2] ** 2

print(r, r_gen)

In [ ]:
scipy.optimize.minimize

In [ ]:
shape = (3, 4)
test = np.random.rand(*shape)
print(test)
print(test.flatten().reshape(shape))

In [ ]:
sigma, rho, beta = 1, 1, 1
x = np.ones((4,3))
np.array([sigma * (x[:, 1] - x[:, 0]),
                 x[:, 0] * (rho - x[:, 2]) - x[:, 1],
                 x[:, 0] * x[:, 1] - beta * x[:, 2]])

In [ ]:
model_array(x)

In [ ]:
a = np.ones((2, 5))
b = np.ones((5,4))

a.shape, b.shape, (a@b).shape